In [1]:
import numpy as np
import pandas as pd
import plotly.express as px
import torch 
import os
import json
import math

import plotly.graph_objects as go

from tools.models import simpleLSTM, simpleLSTM_quantiles
from tools.utils import run_closed_loop, perf_measure, run_closed_loop_quantile

import matplotlib.pyplot as plt


### Iniztialize and load already trained model

In [2]:
settlement      = "Rural-LV1-101-2034"
experiment      = "BaseScenario"
time_horizon    = "0101-3112"
target          = "LV"
model_name      = f'{target}_best_valid_model.pt'

experiment_path = os.path.join('./experiments', settlement, experiment, time_horizon)
lstm_data_path  = os.path.join(experiment_path,"analysis", "lstm", "data")
lstm_model_path = os.path.join(experiment_path, "analysis", "lstm", "model")

model_file = os.path.join(lstm_model_path, model_name)

use_positional_encoding = 'all'
model = simpleLSTM_quantiles(n_input_features=4, num_layers=4)
model.load_state_dict(torch.load(model_file,map_location=torch.device("cpu")))


# Read test data
df_test_scaled_list = []
for i in range(6):
    test_data_path = os.path.join(lstm_data_path, f'{target}_scaled_test{i}.csv')
    df_test_scaled = pd.read_csv(test_data_path, index_col = 0)
    # Convert timestamps to datetime objects 
    datetime_index = pd.to_datetime(df_test_scaled.index)
    df_test_scaled.index = datetime_index
    df_test_scaled_list.append(df_test_scaled)

# Read scalings
scaling_data_path = os.path.join(lstm_data_path,f'{target}_scalings.json')
with open(scaling_data_path, 'r') as file:
    scaling_dict = json.load(file)

### Plot Train and Validation Loss curve, learning rate scheduledf

In [3]:
history_path = os.path.join(lstm_model_path, f'{target}_train_history.csv')
df_train_history = pd.read_csv(history_path, index_col=0)

fig = px.line(df_train_history, x = 'epoch', y = ['train_loss', 'valid_loss'])
fig.show()

fig = px.line(df_train_history, x = 'epoch', y = ['learning_rate'])
fig.show()

### Midterm-forcasting comparison 
Between irradiance forecasts and (imaginary result of having the original irradiance)

In [17]:

# prepare scalings to rescale original power profile:
max_power = scaling_dict[target]['max']
min_power = scaling_dict[target]['min']

max_irradiance = scaling_dict['irradiance_real']['max']
min_irradiance = scaling_dict['irradiance_real']['min']

max_irradiance_fc = scaling_dict['irradiance_fc']['max']
min_irradiance_fc = scaling_dict['irradiance_fc']['min']

months = ['july', 'august', 'september', 'october', 'november', 'december']

MAE_list_original_irradiance = []
RMSE_list_original_irradiance = []

MAE_list_forecast_irradiance = []
RMSE_list_forecast_irradiance  = []

for i in range(6):
    lookback = 96
    test_values = df_test_scaled_list[i].values
    num_test_samples = test_values.shape[0]
    steps2predict = num_test_samples-lookback
    groundtruth = test_values[lookback+1::, 0] # There is a + 1 shift in the inference loop
    #groundtruth = test_values[lookback:-1, 0] 
    time = pd.Series(df_test_scaled_list[i].index)[lookback:-1]
    predictions_with_irradiance_fc, predictions_with_irradiance_fc_quantiles = run_closed_loop_quantile(model, test_values, lookback=lookback, future_prediction=steps2predict, use_positional_encoding='all')
    predictions_with_irradiance_original, predictions_with_irradiance_original_quantiles = run_closed_loop_quantile(model, test_values, lookback=lookback, future_prediction=steps2predict, use_positional_encoding='all_original')


    groundtruth = groundtruth * (max_power - min_power) + min_power #Rescale to orignal values
    predictions_with_irradiance_fc = predictions_with_irradiance_fc * (max_power - min_power) + min_power #Rescale to orignal values
    predictions_with_irradiance_original = predictions_with_irradiance_original * (max_power - min_power) + min_power #Rescale to orignal values
    
    predictions_with_irradiance_fc_quantiles = predictions_with_irradiance_fc_quantiles * (max_power - min_power) + min_power #Rescale to orignal values
    predictions_with_irradiance_original_quantiles = predictions_with_irradiance_original_quantiles * (max_power - min_power) + min_power #Rescale to orignal values

    fig = go.Figure()

    visualization_idx_start = 0
    visualization_idx_stop = visualization_idx_start + 96*14


    fig.add_trace(go.Scatter(x =time[visualization_idx_start:visualization_idx_stop], y= groundtruth[visualization_idx_start:visualization_idx_stop],name = "Groundtruth"))
    fig.add_trace(go.Scatter(x =time[visualization_idx_start:visualization_idx_stop], y= predictions_with_irradiance_fc_quantiles[visualization_idx_start:visualization_idx_stop,5], name = "Prediction"))
    # Add lower boundary line
    fig.add_trace(go.Scatter(
        x=time[visualization_idx_start:visualization_idx_stop],
        y=predictions_with_irradiance_fc_quantiles[visualization_idx_start:visualization_idx_stop, 0],
        mode='lines',
        line=dict(width=0.5, color='darkblue'),
        showlegend=False,
        name='Lower Bound'
    ))

    # Add upper boundary line with fill to the lower boundary line
    fig.add_trace(go.Scatter(
        x=time[visualization_idx_start:visualization_idx_stop],
        y=predictions_with_irradiance_fc_quantiles[visualization_idx_start:visualization_idx_stop, -1],
        mode='lines',
        fill='tonexty', # This fills the area between this line and the previous line
        fillcolor='rgba(0, 0, 139, 0.2)', # Adjust the fill color and alpha here
        line=dict(width=0.5, color='darkblue'),
        showlegend=False,
        name='Upper Bound'
    ))
    # ad title
    fig.update_layout(title_text="Prediction with forecasted weather")
    fig.show()

    fig = go.Figure()

    visualization_idx_start = 0
    visualization_idx_stop = visualization_idx_start + 96*14

    fig.add_trace(go.Scatter(x =time[visualization_idx_start:visualization_idx_stop], y= groundtruth[visualization_idx_start:visualization_idx_stop],name = "Groundtruth"))
    fig.add_trace(go.Scatter(x =time[visualization_idx_start:visualization_idx_stop], y= predictions_with_irradiance_original_quantiles[visualization_idx_start:visualization_idx_stop,5], name = "Real weather"))
    # Add lower boundary line
    fig.add_trace(go.Scatter(
        x=time[visualization_idx_start:visualization_idx_stop],
        y=predictions_with_irradiance_original_quantiles[visualization_idx_start:visualization_idx_stop, 0],
        mode='lines',
        line=dict(width=0.5, color='darkblue'),
        showlegend=False,
        name='Lower Bound'
    ))

    # Add upper boundary line with fill to the lower boundary line
    fig.add_trace(go.Scatter(
        x=time[visualization_idx_start:visualization_idx_stop],
        y=predictions_with_irradiance_original_quantiles[visualization_idx_start:visualization_idx_stop, -1],
        mode='lines',
        fill='tonexty', # This fills the area between this line and the previous line
        fillcolor='rgba(0, 0, 139, 0.2)', # Adjust the fill color and alpha here
        line=dict(width=0.5, color='darkblue'),
        showlegend=False,
        name='Upper Bound'
    ))
    fig.update_layout(title_text="Prediction with real weather")
    fig.show()
   

    squared_error_forecast = (predictions_with_irradiance_fc-groundtruth)**2
    squared_error_original = (predictions_with_irradiance_original-groundtruth)**2
    absolute_error_forecast = np.abs(groundtruth - predictions_with_irradiance_fc)
    absolute_error_original = np.abs(groundtruth - predictions_with_irradiance_original)

    absolute_percentage_eror_forecast = np.abs((groundtruth - predictions_with_irradiance_fc)/groundtruth)
    absolute_percentage_eror_original = np.abs((groundtruth - predictions_with_irradiance_original)/groundtruth)



    mse_original_irradiance = squared_error_original.mean()
    mse_forecast_irradiance = squared_error_forecast.mean()

    mae_original_irradiance = absolute_error_original.mean()
    mae_forecast_irradiance = absolute_error_forecast.mean()

    rmse_original_irradiance = math.sqrt(mse_original_irradiance)
    #rmse_original_irradiance = mse_original_irradiance
    rmse_forecast_irradiance = math.sqrt(mse_forecast_irradiance)
    #rmse_forecast_irradiance = mse_forecast_irradiance

    print('RMSE with irradiance original:', rmse_original_irradiance) 
    print('RMSE with irradiance fc:', rmse_forecast_irradiance)
    print('MAE with irradiance original:', mae_original_irradiance) 
    print('MAE with irradiance fc:', mae_forecast_irradiance)

    MAE_list_original_irradiance.append(mae_original_irradiance)
    RMSE_list_original_irradiance.append(rmse_original_irradiance)

    MAE_list_forecast_irradiance.append(mae_forecast_irradiance)
    RMSE_list_forecast_irradiance.append(rmse_forecast_irradiance)
    #print(f'MSE increases due to uncertainty of irradiance by: {mse_forecast_irradiance/mse_original_irradiance}')

[[0.75959642 0.34510357 0.99993631 0.         0.        ]
 [0.75974415 0.34568912 0.01000304 0.         0.        ]
 [0.76387884 0.34751278 0.0202633  0.         0.        ]
 ...
 [0.76066115 0.32732476 0.96740278 0.         0.        ]
 [0.76101461 0.32401077 0.9780112  0.         0.        ]
 [0.7605872  0.32196953 0.98869595 0.         0.        ]]


RMSE with irradiance original: 12.00994984606852
RMSE with irradiance fc: 24.40718821125918
MAE with irradiance original: 7.639650314267995
MAE with irradiance fc: 13.931722180343437
[[7.64152343e-01 2.89678451e-01 3.84189671e-04 0.00000000e+00
  0.00000000e+00]
 [7.58408736e-01 2.90395281e-01 1.17177711e-02 0.00000000e+00
  0.00000000e+00]
 [7.61707729e-01 2.92473631e-01 2.30054531e-02 0.00000000e+00
  0.00000000e+00]
 ...
 [7.64685167e-01 2.54148230e-01 9.67427296e-01 0.00000000e+00
  0.00000000e+00]
 [7.65047957e-01 2.50914290e-01 9.79485356e-01 0.00000000e+00
  0.00000000e+00]
 [7.62592529e-01 2.49129259e-01 9.91641820e-01 0.00000000e+00
  0.00000000e+00]]


RMSE with irradiance original: 14.435446668638503
RMSE with irradiance fc: 38.639742968890374
MAE with irradiance original: 8.62864473549221
MAE with irradiance fc: 20.520157456868425
[[7.64226004e-01 2.06262428e-01 8.32540313e-03 0.00000000e+00
  0.00000000e+00]
 [7.62768551e-01 2.08039971e-01 2.14921966e-02 0.00000000e+00
  0.00000000e+00]
 [7.61058423e-01 2.11384845e-01 3.45358671e-02 0.00000000e+00
  0.00000000e+00]
 ...
 [7.64539931e-01 1.61803590e-01 9.71335589e-01 0.00000000e+00
  0.00000000e+00]
 [7.66670321e-01 1.59174473e-01 9.85758206e-01 0.00000000e+00
  0.00000000e+00]
 [7.67013792e-01 1.58285326e-01 6.55485061e-05 0.00000000e+00
  0.00000000e+00]]


RMSE with irradiance original: 21.39097926869131
RMSE with irradiance fc: 32.79860884062473
MAE with irradiance original: 12.685814926095615
MAE with irradiance fc: 19.63990075882064
[[0.76197327 0.11867888 0.02033691 0.         0.        ]
 [0.76824735 0.12204548 0.03604359 0.         0.        ]
 [0.76541418 0.12724004 0.05142378 0.         0.        ]
 ...
 [0.78766613 0.07619813 0.97274346 0.         0.        ]
 [0.76737865 0.0739368  0.99041599 0.         0.        ]
 [0.76795135 0.07381153 0.0079902  0.         0.        ]]


RMSE with irradiance original: 22.54037918263153
RMSE with irradiance fc: 23.262700466738792
MAE with irradiance original: 15.287483092935362
MAE with irradiance fc: 15.884313578040418
[[0.79172015 0.04142854 0.02765615 0.         0.        ]
 [0.79534662 0.04587023 0.04677236 0.         0.        ]
 [0.80983681 0.05247913 0.06518609 0.         0.        ]
 ...
 [0.75796567 0.0167446  0.9605839  0.         0.        ]
 [0.77138258 0.01325196 0.98172969 0.         0.        ]
 [0.76751588 0.0123163  0.00303123 0.         0.        ]]


RMSE with irradiance original: 12.769703860370134
RMSE with irradiance fc: 17.824079259433447
MAE with irradiance original: 8.943315022234835
MAE with irradiance fc: 11.875848602449476
[[7.73324280e-01 4.40540414e-04 1.68772450e-02 0.00000000e+00
  0.00000000e+00]
 [7.74029668e-01 3.80610751e-03 3.90639367e-02 0.00000000e+00
  0.00000000e+00]
 [7.74407447e-01 9.71807502e-03 6.03950545e-02 0.00000000e+00
  0.00000000e+00]
 ...
 [7.68253922e-01 9.52297422e-03 9.39183303e-01 0.00000000e+00
  0.00000000e+00]
 [7.73729692e-01 3.55751484e-03 9.60518726e-01 0.00000000e+00
  0.00000000e+00]
 [7.60973655e-01 1.37751079e-04 9.82721191e-01 0.00000000e+00
  0.00000000e+00]]


RMSE with irradiance original: 14.212131687568121
RMSE with irradiance fc: 18.532731206043508
MAE with irradiance original: 10.058190431195495
MAE with irradiance fc: 12.726166207230868
